In [1]:
import tensorflow as tf
from tensorflow.keras import models, layers
import matplotlib.pyplot as plt

In [2]:
#here all images are of same size so we are not resizing it
BATCH_SIZE = 32
IMAGE_SIZE = 256
CHANNELS=3
EPOCHS=50

In [3]:
dataset = tf.keras.preprocessing.image_dataset_from_directory(
    "PlantVillage",
    seed=123,
    shuffle=True,
    image_size=(IMAGE_SIZE,IMAGE_SIZE),
    batch_size=BATCH_SIZE
)# we get "tf.keras.preprocessing.image_dataset_from_directory" about this in tensorflow website

Found 2152 files belonging to 3 classes.


In [9]:
dataset_classes=dataset.class_names
dataset_classes

['Potato___Early_blight', 'Potato___Late_blight', 'Potato___healthy']

In [11]:
len(dataset)# Its are because of batchsizze we know why we use tf_dataset

68

In [13]:
68*32


2176

In [14]:
for image_batch, labels_batch in dataset.take(1):
    print(image_batch.shape)
    print(labels_batch.numpy())#every time we get image we have to convert it into numpy array 

(32, 256, 256, 3)
[1 1 1 0 0 0 0 0 1 1 1 1 0 1 0 1 1 1 0 1 0 1 0 0 1 0 0 1 1 2 0 0]


In [15]:
#0 means Potato___Early_blight',
#1 means 'Potato___Late_blight', 
#2 means 'Potato___healthy

In [17]:
for image_batch, labels_batch in dataset.take(1):
    print(image_batch[0].numpy())
    

[[[161. 146. 151.]
  [147. 132. 137.]
  [143. 128. 133.]
  ...
  [162. 142. 151.]
  [163. 143. 152.]
  [164. 144. 153.]]

 [[146. 131. 136.]
  [147. 132. 137.]
  [145. 130. 135.]
  ...
  [163. 143. 152.]
  [164. 144. 153.]
  [165. 145. 154.]]

 [[145. 130. 135.]
  [147. 132. 137.]
  [147. 132. 137.]
  ...
  [162. 142. 151.]
  [163. 143. 152.]
  [163. 143. 152.]]

 ...

 [[180. 166. 166.]
  [182. 168. 168.]
  [182. 168. 168.]
  ...
  [174. 159. 164.]
  [171. 156. 161.]
  [169. 154. 159.]]

 [[173. 159. 159.]
  [180. 166. 166.]
  [183. 169. 169.]
  ...
  [177. 162. 167.]
  [173. 158. 163.]
  [170. 155. 160.]]

 [[160. 146. 146.]
  [172. 158. 158.]
  [179. 165. 165.]
  ...
  [178. 163. 168.]
  [175. 160. 165.]
  [172. 157. 162.]]]


In [21]:
for image_batch, labels_batch in dataset.take(1):
    print(image_batch[0])
    print(image_batch[0].shape)

    

tf.Tensor(
[[[148. 142. 144.]
  [148. 142. 144.]
  [147. 141. 143.]
  ...
  [169. 164. 168.]
  [168. 163. 167.]
  [165. 160. 164.]]

 [[148. 142. 144.]
  [148. 142. 144.]
  [148. 142. 144.]
  ...
  [170. 165. 169.]
  [168. 163. 167.]
  [164. 159. 163.]]

 [[149. 143. 145.]
  [149. 143. 145.]
  [148. 142. 144.]
  ...
  [169. 164. 168.]
  [165. 160. 164.]
  [160. 155. 159.]]

 ...

 [[138. 130. 128.]
  [133. 125. 123.]
  [131. 123. 121.]
  ...
  [165. 159. 161.]
  [170. 164. 166.]
  [163. 157. 159.]]

 [[137. 129. 127.]
  [133. 125. 123.]
  [133. 125. 123.]
  ...
  [167. 161. 163.]
  [170. 164. 166.]
  [161. 155. 157.]]

 [[139. 131. 129.]
  [136. 128. 126.]
  [136. 128. 126.]
  ...
  [165. 159. 161.]
  [168. 162. 164.]
  [157. 151. 153.]]], shape=(256, 256, 3), dtype=float32)
(256, 256, 3)


In [19]:
#The key difference between tensors and NumPy arrays
#is that tensors have accelerator support like GPU and TPU and
# are immutable

In [23]:
plt.figure(figsize=(10, 10))
for image_batch, labels_batch in dataset.take(1):
    for i in range(12):
        ax = plt.subplot(3, 4, i + 1)#   subplot
        plt.imshow(image_batch[i].numpy().astype("uint8"))# unsigned integer number stored with 8 bit ,it is in float so we converted it into int
        plt.title(dataset_classes[labels_batch[i]])
        plt.axis("off")

In [24]:
#in tensorflow we dont have directly "split " to split data set

In [25]:
#Dataset should be bifurcated into 3 subsets, namely:

#Training: Dataset to be used while training
#Validation: Dataset to be tested against while training
#Test: Dataset to be tested against after we trained a model

In [26]:
len(dataset)

68

In [27]:
train_size = 0.8
len(dataset)*train_size

54.400000000000006

In [28]:
train_ds = dataset.take(54)#slicing [:54]
len(train_ds)

54

In [29]:
test_ds = dataset.skip(54)#[54:}]
len(test_ds)

14

In [30]:
val_size=0.1
len(dataset)*val_size

6.800000000000001

In [31]:
val_ds = test_ds.take(6)
len(val_ds)

6

In [32]:
test_ds = test_ds.skip(6)
len(test_ds)

8

In [33]:
# we dont havee specific data set in tensorflow to split dataset

In [34]:
def get_dataset_partitions_tf(ds, train_split=0.8, val_split=0.1, test_split=0.1, shuffle=True, shuffle_size=10000):
    assert (train_split + test_split + val_split) == 1
    
    ds_size = len(ds)
    
    if shuffle:
        ds = ds.shuffle(shuffle_size, seed=12)
    
    train_size = int(train_split * ds_size)
    val_size = int(val_split * ds_size)
    
    train_ds = ds.take(train_size)    
    val_ds = ds.skip(train_size).take(val_size)
    test_ds = ds.skip(train_size).skip(val_size)
    
    return train_ds, val_ds, test_ds

In [35]:
train_ds, val_ds, test_ds = get_dataset_partitions_tf(dataset)


In [36]:
len(train_ds)

54

In [37]:
len(val_ds)

6

In [38]:
train_ds = train_ds.cache().shuffle(1000).prefetch(buffer_size=tf.data.AUTOTUNE)
val_ds = val_ds.cache().shuffle(1000).prefetch(buffer_size=tf.data.AUTOTUNE)
test_ds = test_ds.cache().shuffle(1000).prefetch(buffer_size=tf.data.AUTOTUNE)

In [39]:
#scaling


In [40]:
resize_and_rescale = tf.keras.Sequential([
  layers.experimental.preprocessing.Resizing(IMAGE_SIZE, IMAGE_SIZE),
  layers.experimental.preprocessing.Rescaling(1./255),
])# why we are again rescaling because  when we give image with not of size 256 it will take cake of it

In [41]:
#can we perform data argumentation using image data generater api class ? yes
data_augmentation = tf.keras.Sequential([
  layers.experimental.preprocessing.RandomFlip("horizontal_and_vertical"),
  layers.experimental.preprocessing.RandomRotation(0.2),
])

In [42]:
input_shape = (BATCH_SIZE, IMAGE_SIZE, IMAGE_SIZE, CHANNELS)
n_classes = 3

model = models.Sequential([
    resize_and_rescale,
    layers.Conv2D(32, kernel_size = (3,3), activation='relu', input_shape=input_shape),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64,  kernel_size = (3,3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64,  kernel_size = (3,3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Flatten(),
    layers.Dense(64, activation='relu'),
    layers.Dense(n_classes, activation='softmax'),
])

model.build(input_shape=input_shape)

In [43]:
model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 sequential (Sequential)     (32, 256, 256, 3)         0         
                                                                 
 conv2d (Conv2D)             (32, 254, 254, 32)        896       
                                                                 
 max_pooling2d (MaxPooling2  (32, 127, 127, 32)        0         
 D)                                                              
                                                                 
 conv2d_1 (Conv2D)           (32, 125, 125, 64)        18496     
                                                                 
 max_pooling2d_1 (MaxPoolin  (32, 62, 62, 64)          0         
 g2D)                                                            
                                                                 
 conv2d_2 (Conv2D)           (32, 60, 60, 64)         

In [44]:
model.compile(
    optimizer='adam',
    loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=False),
    metrics=['accuracy']
)

In [45]:
history = model.fit(
    train_ds,
    batch_size=BATCH_SIZE,
    validation_data=val_ds,
    verbose=1,
    epochs=50,
)

Epoch 1/50
54/54 [==============================] - 69s 1s/step - loss: 0.9061 - accuracy: 0.4821 - val_loss: 0.8459 - val_accuracy: 0.6250
Epoch 2/50
54/54 [==============================] - 61s 1s/step - loss: 0.6235 - accuracy: 0.7095 - val_loss: 0.8499 - val_accuracy: 0.6979
Epoch 3/50
54/54 [==============================] - 63s 1s/step - loss: 0.4644 - accuracy: 0.8102 - val_loss: 0.3616 - val_accuracy: 0.8385
Epoch 4/50
54/54 [==============================] - 61s 1s/step - loss: 0.3186 - accuracy: 0.8640 - val_loss: 0.2148 - val_accuracy: 0.9167
Epoch 5/50
54/54 [==============================] - 54s 999ms/step - loss: 0.2479 - accuracy: 0.9074 - val_loss: 0.1939 - val_accuracy: 0.9062
Epoch 6/50
54/54 [==============================] - 54s 996ms/step - loss: 0.2026 - accuracy: 0.9120 - val_loss: 0.1901 - val_accuracy: 0.9375
Epoch 7/50
54/54 [==============================] - 53s 986ms/step - loss: 0.1441 - accuracy: 0.9427 - val_loss: 0.0984 - val_accuracy: 0.9792
Epoch 8/50


In [46]:
# callback is an object that can perform actions at various stages of training
#(e.g. at the start or end of an epoch, before or after a single batch, etc).

In [47]:
#fit() returns history object
#A History object. Its History.history attribute is a record of training loss values and metrics values at successive epochs, 
#as well as validation loss values and validation metrics values (if applicable).



In [48]:
scores = model.evaluate(test_ds)

8/8 [==============================] - 8s 670ms/step - loss: 9.9149e-06 - accuracy: 1.0000


In [49]:
scores

[9.914871952787507e-06, 1.0]

In [50]:
history

In [51]:
history.params

{'verbose': 1, 'epochs': 50, 'steps': 54}

In [52]:
history.history.keys()

dict_keys(['loss', 'accuracy', 'val_loss', 'val_accuracy'])

In [53]:
(history.history['loss'])


[0.906109094619751,
 0.6234946846961975,
 0.46435219049453735,
 0.3185589015483856,
 0.24794501066207886,
 0.20262032747268677,
 0.14411114156246185,
 0.13603843748569489,
 0.12112542241811752,
 0.0573861189186573,
 0.08237722516059875,
 0.05169765651226044,
 0.040805380791425705,
 0.04178979620337486,
 0.014523024670779705,
 0.04745021089911461,
 0.05552365258336067,
 0.018318936228752136,
 0.1113559827208519,
 0.051017601042985916,
 0.007508298847824335,
 0.00224673212505877,
 0.0008897316292859614,
 0.0002800162183120847,
 0.0001761054591042921,
 0.00013453967403620481,
 0.00010619471140671521,
 8.60431682667695e-05,
 7.105203985702246e-05,
 6.111253605922684e-05,
 5.133445665705949e-05,
 4.358489240985364e-05,
 3.586622915463522e-05,
 3.170943818986416e-05,
 2.6821993742487393e-05,
 2.3355765733867884e-05,
 2.0580762793542817e-05,
 1.8331726096221246e-05,
 1.6399069863837212e-05,
 1.4792995898460504e-05,
 1.3639814824273344e-05,
 1.21508383017499e-05,
 1.118010186473839e-05,
 1.007

In [54]:
acc = history.history['accuracy']
val_acc = history.history['val_accuracy']

loss = history.history['loss']
val_loss = history.history['val_loss']

In [55]:
plt.figure(figsize=(8, 8))
plt.subplot(1, 2, 1)
plt.plot(range(EPOCHS), acc, label='Training Accuracy')
plt.plot(range(EPOCHS), val_acc, label='Validation Accuracy')
plt.legend(loc='lower right')
plt.title('Training and Validation Accuracy')

plt.subplot(1, 2, 2)
plt.plot(range(EPOCHS), loss, label='Training Loss')
plt.plot(range(EPOCHS), val_loss, label='Validation Loss')
plt.legend(loc='upper right')
plt.title('Training and Validation Loss')
plt.show()

In [59]:
import numpy as np
for images_batch, labels_batch in test_ds.take(1):#test_ds.take(1)indicatesone batch 32 images
    
    first_image = images_batch[0].numpy().astype('uint8')
    first_label = labels_batch[0].numpy()
    
    print("first image to predict")
    plt.imshow(first_image)
    print("actual label:",dataset_classes[first_label])
    
    batch_prediction = model.predict(images_batch)
    print("predicted label:",dataset_classes[np.argmax(batch_prediction[0])])

first image to predict
actual label: Potato___Late_blight
1/1 [==============================] - 1s 736ms/step
predicted label: Potato___Late_blight


In [62]:
print(batch_prediction[0]) #we are applying softmax it gives 3 output so highest probability is our answer

[7.8458092e-05 9.9992156e-01 2.3512811e-13]


In [66]:
def predict(model, img):
    img_array = tf.keras.preprocessing.image.img_to_array(images[i].numpy())
    img_array = tf.expand_dims(img_array, 0)

    predictions = model.predict(img_array)

    predicted_class = dataset_classes[np.argmax(predictions[0])]
    confidence = round(100 * (np.max(predictions[0])), 2)
    return predicted_class, confidence

In [67]:
plt.figure(figsize=(15, 15))
for images, labels in test_ds.take(1):
    for i in range(9):
        ax = plt.subplot(3, 3, i + 1)
        plt.imshow(images[i].numpy().astype("uint8"))
        
        predicted_class, confidence = predict(model, images[i].numpy())
        actual_class = dataset_classes[labels[i]] 
        
        plt.title(f"Actual: {actual_class},\n Predicted: {predicted_class}.\n Confidence: {confidence}%")
        
        plt.axis("off")

1/1 [==============================] - 0s 110ms/step


In [70]:
#model is the architecture


In [71]:
import os
model_version=max([int(i) for i in os.listdir("../models") + [0]])+1
model.save(f"../models/{model_version}")

INFO:tensorflow:Assets written to: ../models/2\assets


INFO:tensorflow:Assets written to: ../models/2\assets


In [72]:
model.save("../potatoes.h5")

C:\Users\91939\pythonlab\Lib\site-packages\keras\src\engine\training.py:3000: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(
